In [1]:
import os
import numpy as np
import pandas as pd

In [2]:
# Path to the directory
folder_path = r"C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips"
#os.chdir(path)

In [3]:
# Iterate over all CSV files in the directory
for file_name in os.listdir(folder_path):
    if file_name.endswith('.csv'):
        file_path = os.path.join(folder_path, file_name)
        df = pd.read_csv(file_path)

        # Proceed if the 'ais_timestamp' column exists
        if 'ais_timestamp' in df.columns:
            # Convert 'ais_timestamp' to datetime
            df['ais_timestamp'] = pd.to_datetime(df['ais_timestamp'])

            # Find the maximum timestamp
            max_time = df['ais_timestamp'].max()

            # Calculate the travel time duration from the maximum timestamp in minutes
            df['travel_time_duration'] = (max_time - df['ais_timestamp']).dt.total_seconds() / 60
            df['travel_time_duration'] = df['travel_time_duration'].round(2)

            # Save the modified DataFrame back to CSV
            df.to_csv(file_path, index=False)

C:\Users\firoj\AppData\Local\Temp\ipykernel_16284\2569512276.py:10: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['ais_timestamp'] = pd.to_datetime(df['ais_timestamp'])
C:\Users\firoj\AppData\Local\Temp\ipykernel_16284\2569512276.py:10: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['ais_timestamp'] = pd.to_datetime(df['ais_timestamp'])
C:\Users\firoj\AppData\Local\Temp\ipykernel_16284\2569512276.py:10: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['ais_timestamp'] = pd.to_datetime(df['ais_timestamp'])
C:\Users\firoj\AppData\Local\Temp\ipykernel_16284\2569512276.py:

In [4]:
import glob
from math import radians, cos, sin, asin, sqrt

def haversine(lat1, lon1, lat2, lon2):
    """
    Calculate the great circle distance in kilometers between two points
    on the earth (specified in decimal degrees)
    """
    # convert decimal degrees to radians
    lat1, lon1, lat2, lon2 = map(radians, [lat1, lon1, lat2, lon2])

    # haversine formula
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    # Radius of earth in kilometers is 6371
    km = 6371 * c
    return km

In [5]:
def calculate_distances(df):
    """
    Calculate distances for a DataFrame and return the updated DataFrame.
    """
    # Check if latitude and longitude columns exist
    if 'lat' not in df.columns or 'lon' not in df.columns:
        raise ValueError("DataFrame must contain 'latitude' and 'longitude' columns")

    # Initialize distance column with zeros
    df['distance'] = 0.0

    # Calculate distances
    for i in range(1, len(df)):
        distance = haversine(df.loc[i-1, 'lat'], df.loc[i-1, 'lon'],
                             df.loc[i, 'lat'], df.loc[i, 'lon'])
        df.loc[i, 'distance'] = round(distance, 2)

    return df

In [6]:
def process_csv_files(directory_path):
    """
    Process all CSV files in the given directory to add a distance column.
    """
    for file in glob.glob(f"{folder_path}/*.csv"):
        df = pd.read_csv(file)
        df_updated = calculate_distances(df)
        df_updated.to_csv(file, index=False)

In [7]:
process_csv_files('folder_path')

In [8]:
def add_destination_columns(csv_path):
    df = pd.read_csv(csv_path)

    if 'lat' not in df.columns or 'lon' not in df.columns:
        raise ValueError("CSV file must contain 'lat' and 'lon' columns")

    destination_lat = df['lat'].iloc[-1]
    destination_lon = df['lon'].iloc[-1]

    df['destination_lat'] = destination_lat
    df['destination_lon'] = destination_lon

    df.to_csv(csv_path, index=False)

In [9]:
def process_all_csv(directory):
    for filename in os.listdir(directory):
        if filename.endswith(".csv"):
            csv_path = os.path.join(directory, filename)
            print(f"Processing {csv_path}...")
            add_destination_columns(csv_path)
            print(f"Updated {csv_path}")

In [10]:
process_all_csv(folder_path)

Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205267690.0_9.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205267690.0_9.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205688000.0_5.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205688000.0_5.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_210529000.0_19.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_210529000.0_19.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211284350.0_3.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211284350.0_3.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211418860.0_16.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102

In [11]:
def add_destination_and_distance_columns(csv_path):
    df = pd.read_csv(csv_path)

    if 'lat' not in df.columns or 'lon' not in df.columns:
        raise ValueError("CSV file must contain 'lat' and 'lon' columns")

    destination_lat = df['lat'].iloc[-1]
    destination_lon = df['lon'].iloc[-1]

    df['destination_lat'] = destination_lat
    df['destination_lon'] = destination_lon

    # Calculate the distance for each row and create a new column
    df['remaining_distance'] = df.apply(lambda row: haversine(row['lat'], row['lon'], row['destination_lat'], row['destination_lon']), axis=1)

    df.to_csv(csv_path, index=False)

In [12]:
def process_all_csv(directory):
    for filename in os.listdir(directory):
        if filename.endswith(".csv"):
            csv_path = os.path.join(directory, filename)
            print(f"Processing {csv_path}...")
            add_destination_and_distance_columns(csv_path)
            print(f"Updated {csv_path}")

In [13]:
process_all_csv(folder_path)

Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205267690.0_9.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205267690.0_9.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205688000.0_5.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_205688000.0_5.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_210529000.0_19.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_210529000.0_19.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211284350.0_3.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211284350.0_3.csv
Processing C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102-102_211418860.0_16.csv...
Updated C:\Users\firoj\OneDrive\Desktop\thesis_test\Thesis_test_01\Trips\102